In [1]:
from kaggle_environments import make, evaluate
import random as r
import numpy as np

# Create the game environment
# Set debug=True to see the errors if your agent refuses to run
env = make("connectx", debug=True)

# List of available default agents
print(list(env.agents))

# Two random agents play one game round
env.run(["random", "random"])

# Show the game

env.render(mode="ipython")

Loading environment football failed: No module named 'gfootball'
['random', 'negamax']


In [2]:
# Selects random valid column
def agent_random(obs, config):
    valid_moves = [col for col in range(config['columns']) if obs.board[col] == 0]
    return r.choice(valid_moves)

# Selects middle column
def agent_middle(obs, config):
    return config['columns']//2

# Selects leftmost valid column
def agent_leftmost(obs, config):
    valid_moves = [col for col in range(config['columns']) if obs.board[col] == 0]
    return valid_moves[0]

In [3]:
env.run([agent_random, agent_leftmost])
env.render(mode="ipython")

In [10]:
# Use default Connect Four setup
config = {'rows': 6, 'columns': 7, 'winning_count': 4}

def get_win_percentages(agent1, agent2, n_rounds=100):
    # Agent 1 goes first (roughly) half the time          
    outcomes = evaluate("connectx", [agent1, agent2], config, [], n_rounds//2)
    # Agent 2 goes first (roughly) half the time      
    outcomes += [[b,a] for [a,b] in evaluate("connectx", [agent2, agent1], config, [], n_rounds-n_rounds//2)]
    
    #print scores
    print("Agent 1 Win Percentage:", np.round(outcomes.count([1,-1])/len(outcomes), 2))
    print("Agent 2 Win Percentage:", np.round(outcomes.count([-1,1])/len(outcomes), 2))
    print("Number of Invalid Plays by Agent 1:", outcomes.count([None, 0]))
    print("Number of Invalid Plays by Agent 2:", outcomes.count([0, None]))

#get_win_percentages(agent1=agent_leftmost, agent2=agent_random)

In [14]:
# game board methods

# drop a piece to a specific column
def drop_piece(grid, drop_col, piece):
    for row in range(config['rows']-1, -1, -1):
        if grid[row][drop_col] == 0:
            grid[row][drop_col] = piece
            break
    return grid

# Returns True if dropping piece in column results in game win
def check_pieces_in_window(window, check_num, piece):
    # check if the window has enough piece and space
    return (window.count(piece) == check_num and window.count(0) == config['winning_count']-check_num)
    
# Helper function for get_heuristic: counts number of windows satisfying specified heuristic conditions
def count_windows(grid, check_num, piece):
    num_windows = 0
    # horizontal
    for row in range(config['rows']):
        for col in range(config['columns']-(config['winning_count']-1)):
            window = list(grid[row, col:col+config['winning_count']])
            if check_pieces_in_window(window, check_num, piece):
                num_windows += 1
    # vertical
    for row in range(config['rows']-(config['winning_count']-1)):
        for col in range(config['columns']):
            window = list(grid[row:row+config['winning_count'], col])
            if check_pieces_in_window(window, check_num, piece):
                num_windows += 1
    # positive diagonal
    for row in range(config['rows']-(config['winning_count']-1)):
        for col in range(config['columns']-(config['winning_count']-1)):
            window = list(grid[range(row, row+config['winning_count']), range(col, col+config['winning_count'])])
            if check_pieces_in_window(window, check_num, piece):
                num_windows += 1
    # negative diagonal
    for row in range(config['winning_count']-1, config['rows']):
        for col in range(config['columns']-(config['winning_count']-1)):
            window = list(grid[range(row, row-config['winning_count'], -1), range(col, col+config['winning_count'])])
            if check_pieces_in_window(window, check_num, piece):
                num_windows += 1
    return num_windows

In [160]:
# agent Game Tree (create different tree )

def calculate_grid_score(grid, piece):
    num_win_windows = count_windows(grid, config['winning_count'], piece)
    num_almost_win_windows = count_windows(grid, config['winning_count']-1, piece)
    num_win2_windows = count_windows(grid, config['winning_count']-2, piece)
    
    num_almost_lose_windows = count_windows(grid, config['winning_count']-1, piece%2+1)
    num_lose2_windows = count_windows(grid, config['winning_count']-2, piece%2+1)
    num_lose_windows = count_windows(grid, config['winning_count'], piece%2+1)
    score = 20000*num_win_windows + 900*num_almost_win_windows \
            +50*num_win2_windows                               \
            -2000*num_almost_lose_windows-60*num_lose2_windows \
            -15000*num_lose_windows
    return score, num_lose_windows>0, num_win_windows>0
    
def find_best_action_rec(grid, drop_col, piece, depth, max_depth):
    new_grid = grid.copy()
    new_grid = drop_piece(new_grid, drop_col, piece)
    
    # if we have arrived max depth, return the score
    if depth >= max_depth-1:
        if depth%2==0:
            grid_score = calculate_grid_score(new_grid, piece)
        else:
            grid_score = calculate_grid_score(new_grid, piece%2+1)
        
        return grid_score
    
    # if not arrived max depth, go deeper
    max_action = -1
    max_score = -100000
    
    min_action = -1
    min_score = 100000
    
    for drop_col in range(config['columns']):
        if grid[0][drop_col] != 0: continue
            
        # calculate scores of each action, and select the action gets max score
        score = find_best_action_rec(new_grid, drop_col, piece%2+1, depth+1, max_depth)
        if depth%2==0:
            if max_action==-1 or score > max_score:
                max_action = drop_col
                max_score = score
        else:
            if min_action==-1 or score < min_score:
                min_action = drop_col
                min_score = score
    if depth%2==0:
        return max_score
    else:
        return min_score
    

def find_best_action(grid, piece, max_depth=2):
    # calculate every score of actions
    scores = {}
    for drop_col in range(config['columns']):
        if grid[0][drop_col] != 0: continue # if the column if full then see next column
            
        # calculate scores of this action
        scores[drop_col] = find_best_action_rec(grid, drop_col, piece, 0, max_depth)

    # find actions that result in max scores
    max_score = max(scores.values())
    best_moves = [key for key in scores.keys() if scores[key] == max_score]
    
    # Select at random from the maximizing actions
    return r.choice(best_moves)
    
def CreateAgent(max_depth):
    
    def MyAgent(obs, config):
        game_board_grid = np.array(obs.board).reshape(config['rows'], config['columns'])
        return find_best_action(game_board_grid, obs.mark, max_depth)
    
    return MyAgent

In [155]:
env.run([CreateAgent(3), CreateAgent(1)])
env.render(mode="ipython")


In [161]:
get_win_percentages(CreateAgent(1), CreateAgent(2), n_rounds=20)
get_win_percentages(CreateAgent(3), CreateAgent(2), n_rounds=20)

Agent 1 Win Percentage: 0.2
Agent 2 Win Percentage: 0.8
Number of Invalid Plays by Agent 1: 0
Number of Invalid Plays by Agent 2: 0
Agent 1 Win Percentage: 0.0
Agent 2 Win Percentage: 1.0
Number of Invalid Plays by Agent 1: 0
Number of Invalid Plays by Agent 2: 0
